## Process DataFrames

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
#uncomment this line if you haven't completed the Foursquare API lab

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
# uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library
from bs4 import BeautifulSoup
import requests
print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


Get data from Wikipedia import to dataframe

In [2]:
# GET request
link = requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M").text
soup = BeautifulSoup(link, 'html.parser' )
table = soup.find('table')

In [3]:
#lists
postal_code = []
borough = []
neighborhood = []

In [4]:
#import data with soup
for row_data in soup.find("table").find_all("tr"):
    cells = row_data.find_all("td")
    if(len(cells) > 0):
        postal_code.append(cells[0].text.strip("\n"))
        borough.append(cells[1].text.strip("\n"))
        neighborhood.append(cells[2].text.strip("\n"))
        
#make dataframe
df = pd.DataFrame({"PostalCode":postal_code,"Borough":borough,"Neighborhood":neighborhood})
df.head()

PostalCode           Borough               Neighborhood
0        M1A      Not assigned                           
1        M2A      Not assigned                           
2        M3A        North York                  Parkwoods
3        M4A        North York           Victoria Village
4        M5A  Downtown Toronto  Regent Park, Harbourfront

Remove cells where Borough is not assigned

In [5]:
df=df[df['Borough']!='Not assigned'].reset_index(drop=True)
df.head()

PostalCode           Borough                                 Neighborhood
0        M3A        North York                                    Parkwoods
1        M4A        North York                             Victoria Village
2        M5A  Downtown Toronto                    Regent Park, Harbourfront
3        M6A        North York             Lawrence Manor, Lawrence Heights
4        M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [6]:
df_grouped = df.groupby(["PostalCode","Borough"], as_index = False).agg(lambda x: ", ".join(x))
df_grouped.head()

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

In [7]:
# when Neighborhood has no value, make it the same as Borough
for i,row in df_grouped.iterrows():
    if row["Neighborhood"] == "Not assigned" or "":
        row["Neighborhood"] = row["Borough"]

df_grouped.head()

PostalCode      Borough                            Neighborhood
0        M1B  Scarborough                          Malvern, Rouge
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2        M1E  Scarborough       Guildwood, Morningside, West Hill
3        M1G  Scarborough                                  Woburn
4        M1H  Scarborough                               Cedarbrae

In [8]:
# size of dataframe
df_grouped.shape

(103, 3)

In [9]:
#load coordinates
geo_df = pd.read_csv("Geospatial_Coordinates.csv")
geo_df.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [10]:
# Change Postal Code to PostalCode
geo_df.rename(columns = {"Postal Code": "PostalCode"}, inplace = True)
geo_df.head()

PostalCode   Latitude  Longitude
0        M1B  43.806686 -79.194353
1        M1C  43.784535 -79.160497
2        M1E  43.763573 -79.188711
3        M1G  43.770992 -79.216917
4        M1H  43.773136 -79.239476

In [11]:
# Combine the original dataframe and the geo dataframe
df_combined = df_grouped.merge(geo_df, on = "PostalCode")
df_combined.head()

PostalCode      Borough                            Neighborhood   Latitude  \
0        M1B  Scarborough                          Malvern, Rouge  43.806686   
1        M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2        M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3        M1G  Scarborough                                  Woburn  43.770992   
4        M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [12]:
# Only data with Toronto in borough name
toronto_df  = df_combined[df_combined["Borough"].str.contains("Toronto")]
toronto_df.head()

PostalCode          Borough                    Neighborhood   Latitude  \
37        M4E     East Toronto                     The Beaches  43.676357   
41        M4K     East Toronto    The Danforth West, Riverdale  43.679557   
42        M4L     East Toronto  India Bazaar, The Beaches West  43.668999   
43        M4M     East Toronto                 Studio District  43.659526   
44        M4N  Central Toronto                   Lawrence Park  43.728020   

    Longitude  
37 -79.293031  
41 -79.352188  
42 -79.315572  
43 -79.340923  
44 -79.388790

In [13]:
# Foursquare information
CLIENT_ID = "VH4Y3X5IM5WJOS02QJ1XLPVFQ4DKELZCZB4IETW4IYXW4DTP"
CLIENT_SECRET = "IMMLM4XLH13RVZ1LOLSY0KBYKWGCZBXTM5ZZGJIXDY0CNY5E"
VERSION = "20180604"

## Explore Neighborhoods in Toronto

In [14]:
def getNearbyVenues(names, latitudes, longitudes):
    radius = 500
    LIMIT = 100
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [15]:
toronto_venues = getNearbyVenues(names=toronto_df['Neighborhood'],
                                   latitudes=toronto_df['Latitude'],
                                   longitudes=toronto_df['Longitude']
                                  )

The Beaches
The Danforth West, Riverdale
India Bazaar, The Beaches West
Studio District
Lawrence Park
Davisville North
North Toronto West
Davisville
Moore Park, Summerhill East
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
Roselawn
Forest Hill North & West
The Annex, North Midtown, Yorkville
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Dufferin, Dovercourt Village
Little Portugal, Trinity
Brockton, Parkdale Village, Exhibition Place
High Park, The Junction South
Parkdale, Ron

In [16]:
toronto_venues.head()

Neighborhood  Neighborhood Latitude  \
0                   The Beaches              43.676357   
1                   The Beaches              43.676357   
2                   The Beaches              43.676357   
3                   The Beaches              43.676357   
4  The Danforth West, Riverdale              43.679557   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -79.293031                   Glen Manor Ravine       43.676821   
1              -79.293031  The Big Carrot Natural Food Market       43.678879   
2              -79.293031                 Grover Pub and Grub       43.679181   
3              -79.293031                       Upper Beaches       43.680563   
4              -79.352188                       MenEssentials       43.677820   

   Venue Longitude     Venue Category  
0       -79.293942              Trail  
1       -79.297734  Health Food Store  
2       -79.297215                Pub  
3       -79.292869       Neighborhood  
4       -79.351265     Cosmetics Shop

In [17]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            54   
Brockton, Parkdale Village, Exhibition Place                           23   
Business reply mail Processing Centre                                  17   
CN Tower, King and Spadina, Railway Lands, Harb...                     15   
Central Bay Street                                                     65   
Christie                                                               17   
Church and Wellesley                                                   77   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             38   
Davisville North                                                        7   
Dufferin, Dovercourt Village                                           17   
First Canadian Place, Underground city                                100   
Forest Hill North & West                                                4   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
India Bazaar, The Beaches West                                         19   
Kensington Market, Chinatown, Grange Park                              56   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               43   
Moore Park, Summerhill East                                             3   
North Toronto West                                                     22   
Parkdale, Roncesvalles                                                 14   
Queen's Park, Ontario Provincial Government                            36   
Regent Park, Harbourfront                                              46   
Richmond, Adelaide, King                                               92   
Rosedale                                                                4   
Roselawn                                                                2   
Runnymede, Swansea                                                     38   
St. James Town                                                         77   
St. James Town, Cabbagetown                                            45   
Stn A PO Boxes                                                         93   
Studio District                                                        40   
Summerhill West, Rathnelly, South Hill, Forest ...                     16   
The Annex, North Midtown, Yorkville                                    24   
The Beaches                                                             4   
The Danforth West, Riverdale                                           42   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         36   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             54   
Brockton, Parkdale Village, Exhibition Place                            23   
Business reply mail Processing Centre                                   17   
CN Tower, King and Spadina, Railway Lands, Harb...                      15   
Central Bay Street                                                      65   
Christie                                                                17   
Church and Wellesley                                                    77   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              38   
Davisville North                    

In [18]:
print(toronto_venues.shape)
toronto_venues.head()

(1613, 7)


Neighborhood  Neighborhood Latitude  \
0                   The Beaches              43.676357   
1                   The Beaches              43.676357   
2                   The Beaches              43.676357   
3                   The Beaches              43.676357   
4  The Danforth West, Riverdale              43.679557   

   Neighborhood Longitude                               Venue  Venue Latitude  \
0              -79.293031                   Glen Manor Ravine       43.676821   
1              -79.293031  The Big Carrot Natural Food Market       43.678879   
2              -79.293031                 Grover Pub and Grub       43.679181   
3              -79.293031                       Upper Beaches       43.680563   
4              -79.352188                       MenEssentials       43.677820   

   Venue Longitude     Venue Category  
0       -79.293942              Trail  
1       -79.297734  Health Food Store  
2       -79.297215                Pub  
3       -79.292869       Neighborhood  
4       -79.351265     Cosmetics Shop

## Analyze Each Neighborhood

In [19]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Yoga Studio  Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0            0                  0        0                   0             0   
1            0                  0        0                   0             0   
2            0                  0        0                   0             0   
3            0                  0        0                   0             0   
4            0                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0           0       0     0    0                 0                   0      0   
1           0       0     0    0                 0                   0      0   
2           0       0     0    0                 0                   0      0   
3           0       0     0    0                 0                   0      0   
4           0       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bistro  \
0                0         0           0                   0       0   
1                0         0           0                   0       0   
2                0         0           0                   0       0   
3                0         0           0                   0       0   
4                0         0           0                   0       0   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0              0          0         0                     0               0   
1              0          0         0                     0               0   
2              0          0         0                     0               0   
3              0          0         0                     0               0   
4              0          0         0                     0               0   

   Brewery  Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0        0                0         0             0              0         0   
1        0                0         0             0              0         0   
2        0                0         0             0              0         0   
3        0                0         0             0              0         0   
4        0                0         0             0              0         0   

   Business Service  Butcher  Café  Cajun / Creole Restaurant  Camera Store  \
0                 0        0     0                          0             0   
1                 0        0     0                          0             0   
2       

In [20]:
toronto_onehot.shape

(1613, 239)

In [21]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio  \
0                                         Berczy Park     0.000000   
1        Brockton, Parkdale Village, Exhibition Place     0.000000   
2               Business reply mail Processing Centre     0.000000   
3   CN Tower, King and Spadina, Railway Lands, Har...     0.000000   
4                                  Central Bay Street     0.015385   
5                                            Christie     0.000000   
6                                Church and Wellesley     0.025974   
7                      Commerce Court, Victoria Hotel     0.000000   
8                                          Davisville     0.000000   
9                                    Davisville North     0.000000   
10                       Dufferin, Dovercourt Village     0.000000   
11             First Canadian Place, Underground city     0.000000   
12                           Forest Hill North & West     0.000000   
13                           Garden District, Ryerson     0.000000   
14  Harbourfront East, Union Station, Toronto Islands     0.000000   
15                      High Park, The Junction South     0.000000   
16                     India Bazaar, The Beaches West     0.000000   
17          Kensington Market, Chinatown, Grange Park     0.000000   
18                                      Lawrence Park     0.000000   
19                           Little Portugal, Trinity     0.023256   
20                        Moore Park, Summerhill East     0.000000   
21                                 North Toronto West     0.045455   
22                             Parkdale, Roncesvalles     0.000000   
23        Queen's Park, Ontario Provincial Government     0.027778   
24                          Regent Park, Harbourfront     0.021739   
25                           Richmond, Adelaide, King     0.000000   
26                                           Rosedale     0.000000   
27                                           Roselawn     0.000000   
28                                 Runnymede, Swansea     0.026316   
29                                     St. James Town     0.000000   
30                        St. James Town, Cabbagetown     0.000000   
31                                     Stn A PO Boxes     0.010753   
32                                    Studio District     0.025000   
33  Summerhill West, Rathnelly, South Hill, Forest...     0.000000   
34                The Annex, North Midtown, Yorkville     0.000000   
35                                        The Beaches     0.000000   
36                       The Danforth West, Riverdale     0.023810   
37           Toronto Dominion Centre, Design Exchange     0.000000   
38                     University of Toronto, Harbord     0.027778   

    Afghan Restaurant   Airport  Airport Food Court  Airport Gate  \
0            0.000000  0.000000            0.000000      0.000000   
1            0.000000  0.000000            0.000000      0.000000   
2            0.000000  0.000000            0.000000      0.000000   
3            0.000000  0.066667            0.066667      0.066667   
4            0.000000  0.000000            0.000000      0.000000   
5            0.000000  0.000000            0.000000      0.000000   
6            0.012987  0.000000            0.000000      0.000000   
7            0.000000  0.000000            0.000000      0.000000   
8            0.000000  0.000000            0.000000      0.000000   
9            0.000000  0.000000            0.000000      0.000000   
10           0.000000  0.000000            0.000000      0.000000   
11           0.000000  0.000000            0.000000      0.000000   
12           0.000000  0.000000            0.000000      0.000000   
13           0.000000  0.000000            0.000000      0.000000   
14           0.000000  0.000000            0.000000      0.000000   
15           0.000000  0.000000            0.000000      0.000000   
16           0.000000  0.000000            0.000000      0.000000  

Print each neighborhood with top 5 most common venues

In [22]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Berczy Park----
                venue  freq
0         Coffee Shop  0.07
1        Cocktail Bar  0.06
2              Bakery  0.04
3  Seafood Restaurant  0.04
4         Cheese Shop  0.04


----Brockton, Parkdale Village, Exhibition Place----
            venue  freq
0            Café  0.13
1     Coffee Shop  0.09
2       Nightclub  0.09
3  Breakfast Spot  0.09
4             Gym  0.04


----Business reply mail Processing Centre----
                  venue  freq
0           Pizza Place  0.06
1      Recording Studio  0.06
2            Smoke Shop  0.06
3            Skate Park  0.06
4  Fast Food Restaurant  0.06


----CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport----
                 venue  freq
0      Airport Service  0.20
1     Airport Terminal  0.13
2             Boutique  0.07
3  Rental Car Location  0.07
4     Sculpture Garden  0.07


----Central Bay Street----
                venue  freq
0         Coffee Shop  0.17
1      Sa

In [23]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [24]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1       Brockton, Parkdale Village, Exhibition Place                  Café   
2              Business reply mail Processing Centre            Smoke Shop   
3  CN Tower, King and Spadina, Railway Lands, Har...       Airport Service   
4                                 Central Bay Street           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0          Cocktail Bar              Beer Bar    Seafood Restaurant   
1        Breakfast Spot             Nightclub           Coffee Shop   
2                Garden            Restaurant         Auto Workshop   
3      Airport Terminal      Sculpture Garden   Rental Car Location   
4    Italian Restaurant        Sandwich Place                  Café   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0            Restaurant                Bakery                  Café   
1         Grocery Store               Stadium          Intersection   
2  Fast Food Restaurant        Farmers Market         Burrito Place   
3                 Plane         Boat or Ferry              Boutique   
4          Burger Joint   Japanese Restaurant        Ice Cream Shop   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0           Cheese Shop         Grocery Store                 Bistro  
1                Bakery    Italian Restaurant             Restaurant  
2      Recording Studio               Brewery                Butcher  
3       Harbor / Marina        Airport Lounge           Airport Gate  
4                   Bar       Thai Restaurant            Salad Place

In [25]:
len(toronto_grouped[toronto_grouped["Seafood Restaurant"] > 0])

12

In [26]:
seafood_df = toronto_grouped[["Neighborhood","Seafood Restaurant"]]
seafood_df.head()

Neighborhood  Seafood Restaurant
0                                        Berczy Park            0.037037
1       Brockton, Parkdale Village, Exhibition Place            0.000000
2              Business reply mail Processing Centre            0.000000
3  CN Tower, King and Spadina, Railway Lands, Har...            0.000000
4                                 Central Bay Street            0.015385

## Cluster Neighborhoods

In [52]:
# set number of clusters
kclusters = 3

toronto_grouped_clustering = seafood_df.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 0, 0, 0, 2, 0, 0, 1, 1, 0])

In [53]:
# add clustering labels
#neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

#toronto_merged = toronto_df
toronto_merged = seafood_df.copy()

toronto_merged["Cluster Labels"] = kmeans.labels_

toronto_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
toronto_merged.head()


Neighborhood  Seafood Restaurant  \
0                                        Berczy Park            0.037037   
1       Brockton, Parkdale Village, Exhibition Place            0.000000   
2              Business reply mail Processing Centre            0.000000   
3  CN Tower, King and Spadina, Railway Lands, Har...            0.000000   
4                                 Central Bay Street            0.015385   

   Cluster Labels  
0               1  
1               0  
2               0  
3               0  
4               2

In [54]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(toronto_venues.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() 

Neighborhood  Seafood Restaurant  Cluster Labels  Neighborhood Latitude  \
0  Berczy Park            0.037037               1              43.644771   
0  Berczy Park            0.037037               1              43.644771   
0  Berczy Park            0.037037               1              43.644771   
0  Berczy Park            0.037037               1              43.644771   
0  Berczy Park            0.037037               1              43.644771   

   Neighborhood Longitude                                      Venue  \
0              -79.373306                                       LCBO   
0              -79.373306       The Keg Steakhouse + Bar - Esplanade   
0              -79.373306                             Fresh On Front   
0              -79.373306                              Meridian Hall   
0              -79.373306  Hockey Hall Of Fame (Hockey Hall of Fame)   

   Venue Latitude  Venue Longitude                 Venue Category  
0       43.642944       -79.372440                   Liquor Store  
0       43.646712       -79.374768                     Restaurant  
0       43.647815       -79.374453  Vegetarian / Vegan Restaurant  
0       43.646292       -79.376022                   Concert Hall  
0       43.646974       -79.377323                         Museum

In [55]:
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged

Neighborhood  Seafood Restaurant  \
17          Kensington Market, Chinatown, Grange Park            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
20                        Moore Park, Summerhill East            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
21                                 North Toronto West            0.000000   
22                             Parkdale, Roncesvalles            0.000000   
22                             Parkdale, Roncesvalles            0.000000   
22                             Parkdale, Roncesvalles            0.000000   
22                             Parkdale, Roncesvalles            0.000000   
21                                 North Toronto West            0.000000   
22                             Parkdale, Roncesvalles            0.000000   
20                        Moore Park, Summerhill East            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
20                        Moore Park, Summerhill East            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little Portugal, Trinity            0.000000   
19                           Little P

In [56]:
address = 'Toronto, CA'

geolocator = Nominatim(user_agent="mke_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [57]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighborhood Latitude'], toronto_merged['Neighborhood Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

#### Cluster 0

In [58]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0]

Neighborhood  Seafood Restaurant  \
17          Kensington Market, Chinatown, Grange Park                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
20                        Moore Park, Summerhill East                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
21                                 North Toronto West                 0.0   
22                             Parkdale, Roncesvalles                 0.0   
22                             Parkdale, Roncesvalles                 0.0   
22                             Parkdale, Roncesvalles                 0.0   
22                             Parkdale, Roncesvalles                 0.0   
21                                 North Toronto West                 0.0   
22                             Parkdale, Roncesvalles                 0.0   
20                        Moore Park, Summerhill East                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
20                        Moore Park, Summerhill East                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little Portugal, Trinity                 0.0   
19                           Little P

#### Cluster 1

In [59]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1]

Neighborhood  Seafood Restaurant  \
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                            Stn A PO Boxes            0.032258   
31                  

#### Cluster 2

In [60]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2]

Neighborhood  Seafood Restaurant  \
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
13                           Garden District, Ryerson            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
14  Harbourfront East, Union Station, Toronto Islands            0.010000   
13                           Garden District, Ryerson            0.010000   
14  Harbourfront East, Union Station,

In [62]:
map_clusters.save('map_clusters.html')